<a href="https://colab.research.google.com/github/subham129/Fake-News-Prediction/blob/main/Fake_News_Prediction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np
import pandas as pd
import re
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score

In [2]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [3]:
print(stopwords.words('english'))

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', '

In [15]:
import pandas as pd
import csv  # Import the csv module

# Try handling potential quoting issues
df = pd.read_csv('train.csv', engine='python', encoding='latin-1',
                 quotechar='"', quoting=csv.QUOTE_MINIMAL, on_bad_lines='warn')

print(df.head())

Skipping line 1501: ',' expected after '"'
Skipping line 3166: field larger than field limit (131072)
Skipping line 16453: field larger than field limit (131072)
Skipping line 22701: field larger than field limit (131072)
Skipping line 1288: Expected 5 fields in line 1288, saw 17
Skipping line 1501: Expected 5 fields in line 1501, saw 8
Skipping line 1504: Expected 5 fields in line 1504, saw 6
Skipping line 1523: Expected 5 fields in line 1523, saw 8
Skipping line 1525: Expected 5 fields in line 1525, saw 8
Skipping line 1533: Expected 5 fields in line 1533, saw 7
Skipping line 1534: Expected 5 fields in line 1534, saw 6
Skipping line 3165: Expected 5 fields in line 3165, saw 8
Skipping line 3166: Expected 5 fields in line 3166, saw 9
Skipping line 3167: Expected 5 fields in line 3167, saw 7
Skipping line 3170: Expected 5 fields in line 3170, saw 6
Skipping line 3171: Expected 5 fields in line 3171, saw 9
Skipping line 3172: Expected 5 fields in line 3172, saw 13
Skipping line 3173: Ex

  id                                              title              author  \
0  0  House Dem Aide: We Didnât Even See Comeyâs...       Darrell Lucus   
1  1  FLYNN: Hillary Clinton, Big Woman on Campus - ...     Daniel J. Flynn   
2  2                  Why the Truth Might Get You Fired  Consortiumnews.com   
3  3  15 Civilians Killed In Single US Airstrike Hav...     Jessica Purkiss   
4  4  Iranian woman jailed for fictional unpublished...      Howard Portnoy   

                                                text label  
0  House Dem Aide: We Didnât Even See Comeyâs...     1  
1  Ever get the feeling your life circles the rou...     0  
2  Why the Truth Might Get You Fired October 29, ...     1  
3  Videos 15 Civilians Killed In Single US Airstr...     1  
4  Print \nAn Iranian woman has been sentenced to...     1  


In [16]:
df.isnull().sum()

id           0
title      685
author    2317
text       196
label      183
dtype: int64

In [17]:
df = df.fillna('')

In [18]:
df['content'] = df['author']+''+ df['title']

In [19]:
df['content']

0        Darrell LucusHouse Dem Aide: We Didnât Even ...
1        Daniel J. FlynnFLYNN: Hillary Clinton, Big Wom...
2        Consortiumnews.comWhy the Truth Might Get You ...
3        Jessica Purkiss15 Civilians Killed In Single U...
4        Howard PortnoyIranian woman jailed for fiction...
                               ...                        
23678    Jerome HudsonRapper T.I.: Trump a âPoster Ch...
23679    Benjamin HoffmanN.F.L. Playoffs: Schedule, Mat...
23680    Michael J. de la Merced and Rachel AbramsMacyâ...
23681    Alex AnsaryNATO, Russia To Hold Parallel Exerc...
23682               David SwansonWhat Keeps the F-35 Alive
Name: content, Length: 23683, dtype: object

In [20]:
x  = df.drop(columns='label', axis=1)
y = df['label']

In [21]:
port_stem = PorterStemmer()

In [22]:
def stemming(content):
  stemmed_content = re.sub('[^a-zA-Z]',' ',content)
  stemmed_content = stemmed_content.lower()
  stemmed_content = stemmed_content.split()
  stemmed_content = [port_stem.stem(word) for word in stemmed_content if not word in stopwords.words('english')]
  stemmed_content = ' '.join(stemmed_content)
  return stemmed_content

In [23]:
df['content'] = df['content'].apply(stemming)


In [24]:
x = df['content'].values
y = df['label'].values

In [27]:
vectorizer = TfidfVectorizer()
vectorizer.fit(x)

x = vectorizer.transform(x)

In [32]:
x_train,x_test,y_train,y_test = train_test_split(x,y,test_size=0.2,random_state=2)

In [34]:
model = LogisticRegression()
model.fit(x_train,y_train)
y_pred = model.predict(x_test)
accuracy_score(y_test,y_pred)

0.95672366476673

In [44]:
x_new = x_test[311]

prediction = model.predict(x_new)
print(prediction)

if (prediction[0]=='0'):
  print('The news is Real')
else:
  print('The news is Fake')


['1']
The news is Fake
